<a href="https://colab.research.google.com/github/yee030/Evaluation-Metrics/blob/main/all_moive.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
import numpy as np
import re
from ast import literal_eval

In [ ]:
movies_data = pd.read_csv('/home/user/kye_pro/nave_all_movie.csv')

print(movies_data.shape)
movies_data.head(5)

(18193, 9)


id       title  score       age                              genre  \
0  12654  1990년 자유부인  10.00  청소년 관람불가                  ['드라마', '멜로/로맨스']   
1  10994     19번째 남자   7.58  청소년 관람불가           ['코미디', '드라마', '멜로/로맨스']   
2  10727      48시간 2   7.68  청소년 관람불가  ['범죄', '액션', '드라마', '코미디', '스릴러']   
3  10630      7월 4일생   9.07   15세 관람가                      ['전쟁', '드라마']   
4  10926  90 벌레먹은 장미   0.00  청소년 관람불가                            ['드라마']   

  director                          actors  \
0      박재호           ['고두심', '강석우', '김흥기']   
1     론 쉘톤  ['케빈 코스트너', '수잔 서랜든', '팀 로빈스']   
2     월터 힐               ['에디 머피', '닉 놀테']   
3   올리버 스톤                       ['톰 크루즈']   
4      노세한                  ['남성훈', '김희아']   

                                             summary  review  
0  권위적인 남편 태연(김흥기 분)과의 사이에 딸 슬아를 둔 선영(고두심 분)은 권태롭...     NaN  
1  마이너 리그팀 중의 하나로 캐롤라이나 리그에서 허덕이던 더럼 불즈팀이 오랫동안 기대...     NaN  
2  형사 잭(Jack Cates: 닉 놀테 분)은 범죄단 두목 아이스맨을 추적하다 번번...     NaN  
3  건실한 청년 론(Ron Kovic: 톰 크루즈 분)은 고교시절 레슬링 선수로 땀 흘...     NaN  
4  대학시절 남자에게 배신당한 정희는 30세가 되도록 남자들의 사랑을 불신하며 독신으로...     NaN

In [ ]:
# 영화 감독 이름에서 특수문자를 제거하고 빈 값은 공백으로 대체.
movies_data['director'] = movies_data['director'].str.replace("[^\w]", "")
movies_data['director'] = movies_data['director'].replace(np.nan, " ")

# 배우 이름에서 특수문자 및 괄호를 제거하고 쉼표를 공백으로 대체.
movies_data['actors'] = movies_data['actors'].str.replace("[\[ | \] | \' | \']", "")
movies_data['actors'] = movies_data['actors'].str.replace(",", " ")
movies_data['actors'] = movies_data['actors'].replace(np.nan, " ")

# 장르에서 특수문자와 괄호를 제거하고 쉼표를 공백으로 대체.
movies_data['genre'] = movies_data['genre'].str.replace("[\[ | \] | \' | \']", "")
movies_data['genre'] = movies_data['genre'].str.replace(",", " ")
movies_data['genre'] = movies_data['genre'].replace(np.nan, " ")

# 영화 연령 등급을 한국의 등급 시스템으로 변환.
movies_data['age'] = movies_data['age'].replace('G', '전체 관람가').replace('PG', '12세 관람가').replace('PG-13', '12세 관람가').replace('R', '15세 관람가').replace('NR', " ")
movies_data['review'] = movies_data['review'].replace(np.nan, " ")

# 영화 제목에서 '상영중'이라는 표시를 제거.
movies_data['title'] = movies_data['title'].str.replace('상영중', " ")

# 영화 요약에서 특수문자를 제거하고 빈 값은 공백으로 대체.
movies_data['summary'] = movies_data['summary'].str.replace('[^\w | \s]', "")
movies_data['summary'] = movies_data['summary'].replace(np.nan, " ")


In [ ]:
movies_data.head(5)

id       title  score       age                              genre  \
0  12654  1990년 자유부인  10.00  청소년 관람불가                  ['드라마'  '멜로/로맨스']   
1  10994     19번째 남자   7.58  청소년 관람불가           ['코미디'  '드라마'  '멜로/로맨스']   
2  10727      48시간 2   7.68  청소년 관람불가  ['범죄'  '액션'  '드라마'  '코미디'  '스릴러']   
3  10630      7월 4일생   9.07   15세 관람가                      ['전쟁'  '드라마']   
4  10926  90 벌레먹은 장미   0.00  청소년 관람불가                            ['드라마']   

  director                          actors  \
0      박재호           ['고두심'  '강석우'  '김흥기']   
1     론 쉘톤  ['케빈 코스트너'  '수잔 서랜든'  '팀 로빈스']   
2     월터 힐               ['에디 머피'  '닉 놀테']   
3   올리버 스톤                       ['톰 크루즈']   
4      노세한                  ['남성훈'  '김희아']   

                                             summary review  
0  권위적인 남편 태연(김흥기 분)과의 사이에 딸 슬아를 둔 선영(고두심 분)은 권태롭...         
1  마이너 리그팀 중의 하나로 캐롤라이나 리그에서 허덕이던 더럼 불즈팀이 오랫동안 기대...         
2  형사 잭(Jack Cates: 닉 놀테 분)은 범죄단 두목 아이스맨을 추적하다 번번...         
3  건실한 청년 론(Ron Kovic: 톰 크루즈 분)은 고교시절 레슬링 선수로 땀 흘...         
4  대학시절 남자에게 배신당한 정희는 30세가 되도록 남자들의 사랑을 불신하며 독신으로...

In [ ]:
#No module named 'nltk'
!pip install nltk

  Using cached nltk-3.8.1-py3-none-any.whl (1.5 MB)
  Using cached joblib-1.3.2-py3-none-any.whl.metadata (5.4 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.9/97.9 kB 3.3 MB/s eta 0:00:00
Using cached joblib-1.3.2-py3-none-any.whl (302 kB)


In [ ]:
import nltk

nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /home/user/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [ ]:
!pip install konlpy

  Using cached konlpy-0.6.0-py2.py3-none-any.whl (19.4 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 465.3/465.3 kB 9.0 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.0/8.0 MB 11.2 MB/s eta 0:00:0000:0100:01


In [ ]:
# summary tokenize
from konlpy.tag import Okt, Kkma
from collections import Counter
from nltk.corpus import stopwords

# 한글 불용어와 영어 불용어를 결합하여 불용어 리스트 만들기.
hangul_sw = ['{', '}', '[', ']', '\’', '?', '!', 'ㄴ', 'ㄹ','\"', ')', '(', '...', '\'','은', '는', '이', '가', ',', '.', '아', '휴', '아이구', '아이쿠', '아이고', '어', '나', '우리', '저희', '따라', '의해', '을', '를', '에', '의', '가', '으로', '로', '에게', '뿐이다', '의거하여', '근거하여', '입각하여', '기준으로', '예하면', '예를 들면', '예를 들자면', '저', '소인', '소생', '저희', '지말고', '하지마', '하지마라', '다른', '물론', '또한', '그리고', '비길수 없다', '해서는 안된다', '뿐만 아니라', '만이 아니다', '만은 아니다', '막론하고', '관계없이', '그치지 않다', '그러나', '그런데', '하지만', '든간에', '논하지 않다', '따지지 않다', '설사', '비록', '더라도', '아니면', '만 못하다', '하는 편이 낫다', '불문하고', '향하여', '향해서', '향하다', '쪽으로', '틈타', '이용하여', '타다', '오르다', '제외하고', '이 외에', '이 밖에', '하여야', '비로소', '한다면 몰라도', '외에도', '이곳', '여기', '부터', '기점으로', '따라서', '할 생각이다', '하려고하다', '이리하여', '그리하여', '그렇게 함으로써', '하지만', '일때', '할때', '앞에서', '중에서', '보는데서', '으로써', '로써', '까지', '해야한다', '일것이다', '반드시', '할줄알다', '할수있다', '할수있어', '임에 틀림없다', '한다면', '등', '등등', '제', '겨우', '단지', '다만', '할뿐', '딩동', '댕그', '대해서', '대하여', '대하면', '훨씬', '얼마나', '얼마만큼', '얼마큼', '남짓', '여', '얼마간', '약간', '다소', '좀', '조금', '다수', '몇', '얼마', '지만', '하물며', '또한', '그러나', '그렇지만', '하지만', '이외에도', '대해 말하자면', '뿐이다', '다음에', '반대로', '반대로 말하자면', '이와 반대로', '바꾸어서 말하면', '바꾸어서 한다면', '만약', '그렇지않으면', '까악', '툭', '딱', '삐걱거리다', '보드득', '비걱거리다', '꽈당', '응당', '해야한다', '에 가서', '각', '각각', '여러분', '각종', '각자', '제각기', '하도록하다', '와', '과', '그러므로', '그래서', '고로', '한 까닭에', '하기 때문에', '거니와', '이지만', '대하여', '관하여', '관한', '과연', '실로', '아니나다를가', '생각한대로', '진짜로', '한적이있다', '하곤하였다', '하', '하하', '허허', '아하', '거바', '와', '오', '왜', '어째서', '무엇때문에', '어찌', '하겠는가', '무슨', '어디', '어느곳', '더군다나', '하물며', '더욱이는', '어느때', '언제', '야', '이봐', '어이', '여보시오', '흐흐', '흥', '휴', '헉헉', '헐떡헐떡', '영차', '여차', '어기여차', '끙끙', '아야', '앗', '아야', '콸콸', '졸졸', '좍좍', '뚝뚝', '주룩주룩', '솨', '우르르', '그래도', '또', '그리고', '바꾸어말하면', '바꾸어말하자면', '혹은', '혹시', '답다', '및', '그에 따르는', '때가 되어', '즉', '지든지', '설령', '가령', '하더라도', '할지라도', '일지라도', '지든지', '몇', '거의', '하마터면', '인젠', '이젠', '된바에야', '된이상', '만큼\t어찌됏든', '그위에', '게다가', '점에서 보아', '비추어 보아', '고려하면', '하게될것이다', '일것이다', '비교적', '좀', '보다더', '비하면', '시키다', '하게하다', '할만하다', '의해서', '연이서', '이어서', '잇따라', '뒤따라', '뒤이어', '결국', '의지하여', '기대여', '통하여', '자마자', '더욱더', '불구하고', '얼마든지', '마음대로', '주저하지 않고', '곧', '즉시', '바로', '당장', '하자마자', '밖에 안된다', '하면된다', '그래', '그렇지', '요컨대', '다시 말하자면', '바꿔 말하면', '즉', '구체적으로', '말하자면', '시작하여', '시초에', '이상', '허', '헉', '허걱', '바와같이', '해도좋다', '해도된다', '게다가', '더구나', '하물며', '와르르', '팍', '퍽', '펄렁', '동안', '이래', '하고있었다', '이었다', '에서', '로부터', '까지', '예하면', '했어요', '해요', '함께', '같이', '더불어', '마저', '마저도', '양자', '모두', '습니다', '가까스로', '하려고하다', '즈음하여', '다른', '다른 방면으로', '해봐요', '습니까', '했어요', '말할것도 없고', '무릎쓰고', '개의치않고', '하는것만 못하다', '하는것이 낫다', '매', '매번', '들', '모', '어느것', '어느', '로써', '갖고말하자면', '어디', '어느쪽', '어느것', '어느해', '어느 년도', '라 해도', '언젠가', '어떤것', '어느것', '저기', '저쪽', '저것', '그때', '그럼', '그러면', '요만한걸', '그래', '그때', '저것만큼', '그저', '이르기까지', '할 줄 안다', '할 힘이 있다', '너', '너희', '당신', '어찌', '설마', '차라리', '할지언정', '할지라도', '할망정', '할지언정', '구토하다', '게우다', '토하다', '메쓰겁다', '옆사람', '퉤', '쳇', '의거하여', '근거하여', '의해', '따라', '힘입어', '그', '다음', '버금', '두번째로', '기타', '첫번째로', '나머지는', '그중에서', '견지에서', '형식으로 쓰여', '입장에서', '위해서', '단지', '의해되다', '하도록시키다', '뿐만아니라', '반대로', '전후', '전자', '앞의것', '잠시', '잠깐', '하면서', '그렇지만', '다음에', '그러한즉', '그런즉', '남들', '아무거나', '어찌하든지', '같다', '비슷하다', '예컨대', '이럴정도로', '어떻게', '만약', '만일', '위에서 서술한바와같이', '인 듯하다', '하지 않는다면', '만약에', '무엇', '무슨', '어느', '어떤', '아래윗', '조차', '한데', '그럼에도 불구하고', '여전히', '심지어', '까지도', '조차도', '하지 않도록', '않기 위하여', '때', '시각', '무렵', '시간', '동안', '어때', '어떠한', '하여금', '네', '예', '우선', '누구', '누가 알겠는가', '아무도', '줄은모른다', '줄은 몰랏다', '하는 김에', '겸사겸사', '하는바', '그런 까닭에', '한 이유는', '그러니', '그러니까', '때문에', '그', '너희', '그들', '너희들', '타인', '것', '것들', '너', '위하여', '공동으로', '동시에', '하기 위하여', '어찌하여', '무엇때문에', '붕붕', '윙윙', '나', '우리', '엉엉', '휘익', '윙윙', '오호', '아하', '어쨋든', '만 못하다\t하기보다는', '차라리', '하는 편이 낫다', '흐흐', '놀라다', '상대적으로 말하자면', '마치', '아니라면', '쉿', '그렇지 않으면', '그렇지 않다면', '안 그러면', '아니었다면', '하든지', '아니면', '이라면', '좋아', '알았어', '하는것도', '그만이다', '어쩔수 없다', '하나', '일', '일반적으로', '일단', '한켠으로는', '오자마자', '이렇게되면', '이와같다면', '전부', '한마디', '한항목', '근거로', '하기에', '아울러', '하지 않도록', '않기 위해서', '이르기까지', '이 되다', '로 인하여', '까닭으로', '이유만으로', '이로 인하여', '그래서', '이 때문에', '그러므로', '그런 까닭에', '알 수 있다', '결론을 낼 수 있다', '으로 인하여', '있다', '어떤것', '관계가 있다', '관련이 있다', '연관되다', '어떤것들', '에 대해', '이리하여', '그리하여', '여부', '하기보다는', '하느니', '하면 할수록', '운운', '이러이러하다', '하구나', '하도다', '다시말하면', '다음으로', '에 있다', '에 달려 있다', '우리', '우리들', '오히려', '하기는한데', '어떻게', '어떻해', '어찌됏어', '어때', '어째서', '본대로', '자', '이', '이쪽', '여기', '이것', '이번', '이렇게말하자면', '이런', '이러한', '이와 같은', '요만큼', '요만한 것', '얼마 안 되는 것', '이만큼', '이 정도의', '이렇게 많은 것', '이와 같다', '이때', '이렇구나', '것과 같이', '끼익', '삐걱', '따위', '와 같은 사람들', '부류의 사람들', '왜냐하면', '중의하나', '오직', '오로지', '에 한하다', '하기만 하면', '도착하다', '까지 미치다', '도달하다', '정도에 이르다', '할 지경이다', '결과에 이르다', '관해서는', '여러분', '하고 있다', '한 후', '혼자', '자기', '자기집', '자신', '우에 종합한것과같이', '총적으로 보면', '총적으로 말하면', '총적으로', '대로 하다', '으로서', '참', '그만이다', '할 따름이다', '쿵', '탕탕', '쾅쾅', '둥둥', '봐', '봐라', '아이야', '아니', '와아', '응', '아이', '참나', '년', '월', '일', '령', '영', '일', '이', '삼', '사', '오', '육', '륙', '칠', '팔', '구', '이천육', '이천칠', '이천팔', '이천구', '하나', '둘', '셋', '넷', '다섯', '여섯', '일곱', '여덟', '아홉', '령', '영', ' ㄴ다']
english_sw = stopwords.words('english') # NLTK를 이용해 영어 불용어 리스트 가져오기.
sw = hangul_sw + english_sw # 한글과 영어 불용어를 결합하여 최종 불용어 리스트 만들기.

sentence = movies_data['summary']# 'summary' 열의 데이터를 가져오기.

for idx, text in enumerate(sentence):
    words = Kkma().nouns(text)  # Konlpy의 Kkma를 사용해 문장을 단어로 토큰화
    nsw_words = []  # 불용어가 제거된 단어를 담을 리스트를 생성

    # 토큰화된 단어들 중 불용어에 해당하지 않는 단어들을 소문자로 변환하여 저장
    for x in words:
        if x not in sw:
            nsw_words.append(x.lower())

    # 불용어가 제거된 단어들을 다시 문장으로 합쳐 해당 열의 값을 업데이트.
    movies_data['summary'][idx] = " ".join(nsw_words)

/tmp/ipykernel_659581/2735178691.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movies_data['summary'][idx] = " ".join(nsw_words)
/tmp/ipykernel_659581/2735178691.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movies_data['summary'][idx] = " ".join(nsw_words)
/tmp/ipykernel_659581/2735178691.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  movies_data['summary'][idx] = " ".join(nsw_words)
/tmp/ipykernel_659581/273517869

In [ ]:
movies_data.to_csv("./movie_data_preprocessing.csv", header=False, index=False, encoding='utf-8')

In [ ]:
movies_data

id       title  score       age                              genre  \
0       12654  1990년 자유부인  10.00  청소년 관람불가                  ['드라마'  '멜로/로맨스']   
1       10994     19번째 남자   7.58  청소년 관람불가           ['코미디'  '드라마'  '멜로/로맨스']   
2       10727      48시간 2   7.68  청소년 관람불가  ['범죄'  '액션'  '드라마'  '코미디'  '스릴러']   
3       10630      7월 4일생   9.07   15세 관람가                      ['전쟁'  '드라마']   
4       10926  90 벌레먹은 장미   0.00  청소년 관람불가                            ['드라마']   
...       ...         ...    ...       ...                                ...   
18188  186347     환상의 마로나   9.12    전체 관람가             ['애니메이션'  '드라마'  '가족']   
18189  192360        후계자들   7.57   15세 관람가                             ['액션']   
18190  191688  후배부부와교환섹스2   0.00  청소년 관람불가                         ['멜로/로맨스']   
18191  182353      후쿠오카     8.43   15세 관람가                            ['드라마']   
18192  185838         히트맨   6.75   15세 관람가                      ['코미디'  '액션']   

       director                                             actors  \
0           박재호                              ['고두심'  '강석우'  '김흥기']   
1          론 쉘톤                     ['케빈 코스트너'  '수잔 서랜든'  '팀 로빈스']   
2          월터 힐                                  ['에디 머피'  '닉 놀테']   
3        올리버 스톤                                          ['톰 크루즈']   
4           노세한                                     ['남성훈'  '김희아']   
...         ...                                                ...   
18188    안카 다미안  ['리지 브로체르'  '브루노 살로몬'  '티에리 한시세'  '나탈리 부테푸'  '...   
18189  로힛 칸 바트라                              ['브렌든 프레이저'  '로닛 로이']   
18190       이정석                                                 []   
18191        장률                   ['권해효'  '윤제문'  '박소담'  '야마모토 유키']   
18192       최원섭               ['권상우'  '정준호'  '황우슬혜'  '이이경'  '이지원']   

                                                 summary review  
0      권위 남편 태연 김 김흥기 흥기 분 과의 사이 딸 선영 고두 고두심 심 권태 일상 ...         
1      마이너 리그 리그팀 팀 중의 캐롤라이 더럼 불즈팀 오랫동안 기대 신인 투수 로빈슨 ...         
2      형사 잭 닉 테 분 범죄 범죄단 단 두목 아이스 아이스맨 맨 추적 허탕 인명 손실 ...         
3      청년 론 톰 크루즈 분 고교 고교시절 시절 레슬링 선수 땀 고통 스파 스파르 르 식...         
4      대학 대학시절 시절 남자 배신 정 30 30세가 세가 사랑 불신 독신 그녀 이혼 지...         
...                                                  ...    ...  
18188  9 9남매 남매 중 막내 마 형제 인간 주인 견 견생의 생의 제2막이 2 막이 곡예...         
18189  인도 유명 마피아 가문 수장 압박 자살 권력 첫째 아들 불만 둘째 무기 밀매 업자 ...         
18190  밤 아내 쥬리 병 병철 철 그녀 성욕 후배 수형 기운 걱정 사정 이야기 예전 고민 ...         
18191  책방 단골 소 소담 담 때문 쑥 후쿠오카 도착 제문 그녀 술집 국화 그곳 28 28...         
18192  웹 웹툰 툰 작가 국정원 탈출 비밀 프로젝트 방패연 출신 전설 암살 암살요원 요원 ...         

[18193 rows x 9 columns]

In [ ]:
import pandas as pd  # 판다스 라이브러리를 임포트
import numpy as np  # 넘파이 라이브러리를 임포트

# './movie_data_preprocessing.csv' 파일에서 데이터를 읽어오기
movies_data = pd.read_csv("./movie_data_preprocessing.csv")

# 데이터프레임의 열(column) 이름을 지정하기
movies_data.columns = ['movie_id', 'title', 'star', 'age', 'genre', 'director', 'actors', 'summary','review']


In [ ]:
# 'director' 열에서 결측값을 공백으로 대체
movies_data['director'] = movies_data['director'].replace(np.nan, " ")

# 'actors' 열에서 결측값을 공백으로 대체
movies_data['actors'] = movies_data['actors'].replace(np.nan, " ")

# 'genre' 열에서 결측값을 공백으로 대체
movies_data['genre'] = movies_data['genre'].replace(np.nan, " ")

# 'movie_rating' 열에서 결측값을 공백으로 대체
movies_data['age'] = movies_data['age'].replace(np.nan, " ")

# 'summary' 열에서 결측값을 공백으로 대체
movies_data['summary'] = movies_data['summary'].replace(np.nan, " ")

# 'review' 열에서 결측값을 공백으로 대체
movies_data['review'] = movies_data['review'].replace(np.nan, " ")


In [ ]:
movies_data

movie_id       title  star       age  \
0         10994     19번째 남자  7.58  청소년 관람불가   
1         10727      48시간 2  7.68  청소년 관람불가   
2         10630      7월 4일생  9.07   15세 관람가   
3         10926  90 벌레먹은 장미  0.00  청소년 관람불가   
4         14478     9일간의 정사  7.00             
...         ...         ...   ...       ...   
18187    186347     환상의 마로나  9.12    전체 관람가   
18188    192360        후계자들  7.57   15세 관람가   
18189    191688  후배부부와교환섹스2  0.00  청소년 관람불가   
18190    182353      후쿠오카    8.43   15세 관람가   
18191    185838         히트맨  6.75   15세 관람가   

                                   genre  director  \
0               ['코미디'  '드라마'  '멜로/로맨스']      론 쉘톤   
1      ['범죄'  '액션'  '드라마'  '코미디'  '스릴러']      월터 힐   
2                          ['전쟁'  '드라마']    올리버 스톤   
3                                ['드라마']       노세한   
4                               ['이탈리아']   브루노 마테이   
...                                  ...       ...   
18187             ['애니메이션'  '드라마'  '가족']    안카 다미안   
18188                             ['액션']  로힛 칸 바트라   
18189                         ['멜로/로맨스']       이정석   
18190                            ['드라마']        장률   
18191                      ['코미디'  '액션']       최원섭   

                                                  actors  \
0                         ['케빈 코스트너'  '수잔 서랜든'  '팀 로빈스']   
1                                      ['에디 머피'  '닉 놀테']   
2                                              ['톰 크루즈']   
3                                         ['남성훈'  '김희아']   
4                                                     []   
...                                                  ...   
18187  ['리지 브로체르'  '브루노 살로몬'  '티에리 한시세'  '나탈리 부테푸'  '...   
18188                              ['브렌든 프레이저'  '로닛 로이']   
18189                                                 []   
18190                   ['권해효'  '윤제문'  '박소담'  '야마모토 유키']   
18191               ['권상우'  '정준호'  '황우슬혜'  '이이경'  '이지원']   

                                                 summary review  
0      마이너 리그 리그팀 팀 중의 캐롤라이 더럼 불즈팀 오랫동안 기대 신인 투수 로빈슨 ...         
1      형사 잭 닉 테 분 범죄 범죄단 단 두목 아이스 아이스맨 맨 추적 허탕 인명 손실 ...         
2      청년 론 톰 크루즈 분 고교 고교시절 시절 레슬링 선수 땀 고통 스파 스파르 르 식...         
3      대학 대학시절 시절 남자 배신 정 30 30세가 세가 사랑 불신 독신 그녀 이혼 지...         
4      미국인 피아니스트 제시 제시카 카 콘테스트 참가 베니스 도착 자격 실격 말 필사적 ...         
...                                                  ...    ...  
18187  9 9남매 남매 중 막내 마 형제 인간 주인 견 견생의 생의 제2막이 2 막이 곡예...         
18188  인도 유명 마피아 가문 수장 압박 자살 권력 첫째 아들 불만 둘째 무기 밀매 업자 ...         
18189  밤 아내 쥬리 병 병철 철 그녀 성욕 후배 수형 기운 걱정 사정 이야기 예전 고민 ...         
18190  책방 단골 소 소담 담 때문 쑥 후쿠오카 도착 제문 그녀 술집 국화 그곳 28 28...         
18191  웹 웹툰 툰 작가 국정원 탈출 비밀 프로젝트 방패연 출신 전설 암살 암살요원 요원 ...         

[18192 rows x 9 columns]

In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity


# 사용자로부터 원하는 카테고리를 선택받는 함수
def get_categories():
    categories_lst = ['title', 'genre', 'director', 'actors']

    categories = list(map(str, input("원하는 카테고리를 고르시오 (title, genre, director, actors) :").split()))
    for categorie in categories:
        if categorie not in categories_lst:
            print("잘못된 카테고리를 입력하였습니다.", end="")
            get_categories()
    else:
        return categories


def get_tfidf_matrix(dataset, categories): #TF-IDF 행렬을 만들고, 각 카테고리에 대해 코사인 유사도를 계산하여 유사한 인덱스를 반환
    attribute = ['movie_rating', 'genre', 'director', 'actors']

    tfidf_vec = TfidfVectorizer(ngram_range=(1, 2))

    similar_index_dic = {categorie:None for categorie in categories}

    for categorie in categories:
        tfidf_matrix = tfidf_vec.fit_transform(dataset['summary'])
        genres_similarity = cosine_similarity(tfidf_matrix, tfidf_matrix) #영화 요약을 기반으로 한 유사도를 계산
        similar_index = np.argsort(-genres_similarity)
        similar_index_dic[categorie] = similar_index

    return similar_index_dic


def find_similar_moive(movies_data, new_user_input): #새로운 사용자 입력에 해당하는 영화의 인덱스를 찾음
    movie_index_list = []

    for categorie, value in new_user_input.items():
        movie_index = movies_data[movies_data[str(categorie)]==value].index.values
        movie_index_list.append(movie_index)

    return movie_index


def find_info(movies_data, categorie, value):
    lengh = movies_data[categorie].shape[0]

    find_lst = []
    if categorie == 'title':
        return movies_data['title']==value
    else:
        for i in range(lengh):
            if value in movies_data[categorie][i].split():
                find_lst.append(True)
            else:
                find_lst.append(False)
        return find_lst


def get_movie_index_lst(movies_data, new_user_input):
    movie_index_lst = []

    for categorie, value in new_user_input.items():
        b = find_info(movies_data, categorie, value)
        movie_index = movies_data[b].index.values
        movie_index_lst.append(movie_index)
    return movie_index_lst


def match_idx(movie_index_lst):
    match_lst = []

    if len(movie_index_lst) == 1:
        return movie_index_lst[0]

    elif len(movie_index_lst) == 2:
        for i in movie_index_lst[0]:
            for j in movie_index_lst[1]:
                if i == j :
                    match_lst.append(i)
                    break
        return match_lst

    elif len(movie_index_lst) == 3:
        for i in movie_index_lst[0]:
            for j in movie_index_lst[1]:
                for k in movie_index_lst[2]:
                    if i == j == k:
                        match_lst.append(i)
                        break
        return match_lst
    else:
        print("입력하신 정보에 의해 추천되는 영화가 없습니다.")

def seach_similar_movie(movies_data, similar_index_dic, match_lst, categories): #유사한 영화들의 인덱스를 찾아 해당하는 영화 정보를 반환
    if len(categories) == 1:
        similar_movies = similar_index_dic[categories[0]][match_lst, : 10]
        similar_movies_index = similar_movies.reshape(-1)
        return movies_data.iloc[similar_movies_index]
    else:
        similar_movies = similar_index_dic[categories[0]][match_lst, : 10].T
        similar_movies_index = similar_movies.reshape(-1)
        return movies_data.iloc[similar_movies_index]

In [ ]:
#transformers 라이브러리설치
!pip install transformers



In [ ]:
#No module named 'sklearn'
!pip install scikit-learn


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 2.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.9/10.9 MB 10.8 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 36.6/36.6 MB 8.1 MB/s eta 0:00:0000:0100:01m


In [ ]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from transformers import pipeline
import numpy as np

# TF-IDF 행렬을 만들고, 각 카테고리에 대해 코사인 유사도를 계산하여 유사한 인덱스를 반환하는 함수
def get_tfidf_matrix(dataset):
    tfidf_vec = TfidfVectorizer(ngram_range=(1, 2))
    tfidf_matrix = tfidf_vec.fit_transform(dataset['summary'])
    genres_similarity = cosine_similarity(tfidf_matrix, tfidf_matrix) # 영화 요약을 기반으로 한 유사도 계산
    similar_index = np.argsort(-genres_similarity)
    return similar_index

# 감정 분석 모델을 초기화
sentiment_analysis = pipeline('sentiment-analysis')

# 영화 요약을 기반으로 감정을 분석하는 함수
def analyze_sentiment(summary):
    result = sentiment_analysis(summary)
    return result[0]['label']

# 영화에 감정 태깅하여 데이터셋에 추가하는 함수
def tag_movie_emotions(movies_data):
    movies_data['emotion'] = movies_data['summary'].apply(analyze_sentiment)
    return movies_data

# 사용자의 요청과 감정 정보를 바탕으로 영화를 추천하는 함수
def recommend_movies(movies_data, current_mood, desired_genre):
    filtered_movies = movies_data[(movies_data['emotion'] == current_mood) & (movies_data['genre'] == desired_genre)]
    return filtered_movies

# 영화 데이터셋에서 감정 태깅을 추가
movies_data = tag_movie_emotions(movies_data)

# 예시: 현재 기분과 원하는 장르에 따라 영화 추천
current_mood = 'positive'  # 현재 기분 설정
desired_genre = 'Action'   # 원하는 장르 설정

recommended_movies = recommend_movies(movies_data, current_mood, desired_genre)
print(recommended_movies)


/home/user/kye_pro/.conda/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
None of PyTorch, TensorFlow >= 2.0, or Flax have been found. Models won't be available and only tokenizers, configuration and file/data utilities can be used.
No model was supplied, defaulted to distilbert-base-uncased-finetuned-sst-2-english and revision af0f99b (https://huggingface.co/distilbert-base-uncased-finetuned-sst-2-english).
Using a pipeline without specifying a model name and revision in production is not recommended.
config.json: 100%|██████████| 629/629 [00:00<00:00, 99.2kB/s]


RuntimeError: At least one of TensorFlow 2.0 or PyTorch should be installed. To install TensorFlow 2.0, read the instructions at https://www.tensorflow.org/install/ To install PyTorch, read the instructions at https://pytorch.org/.

In [ ]:
# 카테고리 목록을 얻어옵니다.
categories = get_categories()

user_input = []

# 각 카테고리에 대한 사용자 입력을 받습니다.
for category in categories:
    user_input.append(input(f"{category} : "))

# 카테고리와 사용자 입력을 매핑하여 딕셔너리로 만듭니다.
new_user_input = {key: value for (key, value) in zip(categories, user_input)}

print("검색중.....")

# TF-IDF 매트릭스를 생성합니다.
similar_index_dic = get_tfidf_matrix(movies_data, categories)

# 사용자 입력에 해당하는 영화 인덱스 리스트를 가져옵니다.
movie_index_lst = get_movie_index_lst(movies_data, new_user_input)

# 유사한 영화 인덱스를 찾습니다.
match_lst = match_idx(movie_index_lst)

# 유사한 영화를 검색하여 상위 10개를 출력합니다.
search_similar_movie(movies_data, similar_index_dic, match_lst, categories)[:10]
